In [1]:
import tensorflow as tf
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split

In [2]:
#load dataset with redundant features removed (see NBA_predictive_model.ipynb)
df_NBA_slim = pd.read_csv('NBA_numeric_slim.csv')
df_NBA_slim.head()

season   age     w   sos  o_rtg  d_rtg  pace   f_tr  x3p_ar  ts_percent  \
0    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   
1    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   
2    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   
3    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   
4    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   

   ...  away_orb_percent  away_opp_e_fg_percent  away_opp_tov_percent  \
0  ...              27.2                  0.481                  14.2   
1  ...              29.5                  0.497                  14.7   
2  ...              28.4                  0.454                  14.4   
3  ...              28.4                  0.482                  15.1   
4  ...              31.2                  0.461                  13.5   

   away_opp_drb_percent  away_opp_ft_fga  away_attend  away_attend_g  \
0                  70.1            0.274     656081.0        16002.0   
1                  70.9            0.269     591701.0        14432.0   
2                  72.6            0.262     828384.0        20204.0   
3                  71.7            0.247     723949.0        17657.0   
4                  73.0            0.207     905116.0        22076.0   

   home_score  away_score  spread  
0         120         117       3  
1          90          93      -3  
2         105         114      -9  
3         110         107       3  
4          68          95     -27  

[5 rows x 38 columns]

In [3]:
#create training and test sets
train_set_r, test_val_set_r = train_test_split(df_NBA_slim, test_size=0.2, 
                                       stratify=df_NBA_slim['season'], random_state=42)

#separate into data (X) and targets(y).  Remove "season" and 'home_score' and 'away_score'
X_train_r = train_set_r.iloc[:,1:-3]
y_train_r = train_set_r.iloc[:,-1]

#split test_val_set into test and validation sets
test_set_r, val_set_r = train_test_split(test_val_set_r, test_size=0.5, 
                                       stratify=test_val_set_r['season'], random_state=42)

X_test_r = test_set_r.iloc[:,1:-3]
y_test_r = test_set_r.iloc[:,-1]

X_val_r = val_set_r.iloc[:,1:-3]
y_val_r = val_set_r.iloc[:,-1]

In [4]:
#z-score normalize the data
ss = StandardScaler()

X_train_r_ss = ss.fit_transform(X_train_r)
X_test_r_ss = ss.transform(X_test_r)
X_val_r_ss = ss.transform(X_val_r)

In [5]:
#display shape of processed data
X_train_r_ss.shape


(9188, 34)

In [7]:
%%time

tf.random.set_seed(42)
model=tf.keras.Sequential([
    tf.keras.layers.Dense(100, input_shape=(34,), activation="relu"),
    tf.keras.layers.Dense(100, activation="relu"),
    tf.keras.layers.Dense(100, activation="relu"),
    tf.keras.layers.Dense(1,)
])
optimizer = tf.keras.optimizers.Adam(learning_rate=1e-3, weight_decay=1e-2)
model.compile(loss="mse", optimizer=optimizer, metrics=["RootMeanSquaredError"])

history = model.fit(X_train_r_ss, y_train_r, epochs=10000,
                    validation_data=(X_val_r_ss, y_val_r))

Epoch 1/10000
288/288 [==============================] - 1s 2ms/step - loss: 155.1830 - root_mean_squared_error: 12.4572 - val_loss: 153.0541 - val_root_mean_squared_error: 12.3715
Epoch 2/10000
288/288 [==============================] - 0s 2ms/step - loss: 148.5675 - root_mean_squared_error: 12.1888 - val_loss: 154.1749 - val_root_mean_squared_error: 12.4167
Epoch 3/10000
288/288 [==============================] - 0s 2ms/step - loss: 147.0470 - root_mean_squared_error: 12.1263 - val_loss: 153.0389 - val_root_mean_squared_error: 12.3709
Epoch 4/10000
288/288 [==============================] - 0s 2ms/step - loss: 145.8673 - root_mean_squared_error: 12.0776 - val_loss: 153.7522 - val_root_mean_squared_error: 12.3997
Epoch 5/10000
288/288 [==============================] - 1s 2ms/step - loss: 143.9691 - root_mean_squared_error: 11.9987 - val_loss: 152.3394 - val_root_mean_squared_error: 12.3426
Epoch 6/10000
288/288 [==============================] - 1s 2ms/step - loss: 142.5803 - root_me

288/288 [==============================] - 1s 2ms/step - loss: 19.3437 - root_mean_squared_error: 4.3981 - val_loss: 261.3861 - val_root_mean_squared_error: 16.1674
Epoch 92/10000
288/288 [==============================] - 1s 2ms/step - loss: 16.9427 - root_mean_squared_error: 4.1162 - val_loss: 266.5808 - val_root_mean_squared_error: 16.3273
Epoch 93/10000
288/288 [==============================] - 1s 2ms/step - loss: 16.0365 - root_mean_squared_error: 4.0046 - val_loss: 268.8333 - val_root_mean_squared_error: 16.3961
Epoch 94/10000
288/288 [==============================] - 1s 2ms/step - loss: 16.3501 - root_mean_squared_error: 4.0435 - val_loss: 275.1302 - val_root_mean_squared_error: 16.5870
Epoch 95/10000
288/288 [==============================] - 1s 2ms/step - loss: 16.6100 - root_mean_squared_error: 4.0755 - val_loss: 278.7081 - val_root_mean_squared_error: 16.6946
Epoch 96/10000
288/288 [==============================] - 1s 2ms/step - loss: 16.5961 - root_mean_squared_error: 4.

288/288 [==============================] - 1s 2ms/step - loss: 8.2828 - root_mean_squared_error: 2.8780 - val_loss: 274.6639 - val_root_mean_squared_error: 16.5730
Epoch 182/10000
288/288 [==============================] - 1s 2ms/step - loss: 7.7469 - root_mean_squared_error: 2.7833 - val_loss: 273.3615 - val_root_mean_squared_error: 16.5336
Epoch 183/10000
288/288 [==============================] - 1s 2ms/step - loss: 9.0316 - root_mean_squared_error: 3.0053 - val_loss: 272.1519 - val_root_mean_squared_error: 16.4970
Epoch 184/10000
288/288 [==============================] - 1s 2ms/step - loss: 9.8987 - root_mean_squared_error: 3.1462 - val_loss: 269.8319 - val_root_mean_squared_error: 16.4266
Epoch 185/10000
288/288 [==============================] - 1s 2ms/step - loss: 8.5559 - root_mean_squared_error: 2.9250 - val_loss: 273.2016 - val_root_mean_squared_error: 16.5288
Epoch 186/10000
288/288 [==============================] - 1s 2ms/step - loss: 8.1155 - root_mean_squared_error: 2.8

288/288 [==============================] - 1s 2ms/step - loss: 6.3966 - root_mean_squared_error: 2.5292 - val_loss: 267.4927 - val_root_mean_squared_error: 16.3552
Epoch 272/10000
288/288 [==============================] - 1s 2ms/step - loss: 6.4142 - root_mean_squared_error: 2.5326 - val_loss: 268.9187 - val_root_mean_squared_error: 16.3987
Epoch 273/10000
288/288 [==============================] - 1s 2ms/step - loss: 6.9658 - root_mean_squared_error: 2.6393 - val_loss: 264.2417 - val_root_mean_squared_error: 16.2555
Epoch 274/10000
288/288 [==============================] - 1s 2ms/step - loss: 6.2030 - root_mean_squared_error: 2.4906 - val_loss: 261.0943 - val_root_mean_squared_error: 16.1584
Epoch 275/10000
288/288 [==============================] - 1s 2ms/step - loss: 6.4697 - root_mean_squared_error: 2.5436 - val_loss: 270.2686 - val_root_mean_squared_error: 16.4398
Epoch 276/10000
288/288 [==============================] - 1s 2ms/step - loss: 6.7181 - root_mean_squared_error: 2.5

288/288 [==============================] - 1s 2ms/step - loss: 5.9721 - root_mean_squared_error: 2.4438 - val_loss: 259.4820 - val_root_mean_squared_error: 16.1084
Epoch 362/10000
288/288 [==============================] - 1s 2ms/step - loss: 6.1959 - root_mean_squared_error: 2.4892 - val_loss: 256.2290 - val_root_mean_squared_error: 16.0072
Epoch 363/10000
288/288 [==============================] - 1s 2ms/step - loss: 6.0942 - root_mean_squared_error: 2.4686 - val_loss: 265.0425 - val_root_mean_squared_error: 16.2801
Epoch 364/10000
288/288 [==============================] - 1s 2ms/step - loss: 5.6113 - root_mean_squared_error: 2.3688 - val_loss: 265.8089 - val_root_mean_squared_error: 16.3036
Epoch 365/10000
288/288 [==============================] - 1s 2ms/step - loss: 5.0256 - root_mean_squared_error: 2.2418 - val_loss: 257.2437 - val_root_mean_squared_error: 16.0388
Epoch 366/10000
288/288 [==============================] - 1s 2ms/step - loss: 5.5474 - root_mean_squared_error: 2.3

...

288/288 [==============================] - 1s 2ms/step - loss: 2.7509 - root_mean_squared_error: 1.6586 - val_loss: 228.0965 - val_root_mean_squared_error: 15.1029
Epoch 9632/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.5617 - root_mean_squared_error: 1.6005 - val_loss: 231.7334 - val_root_mean_squared_error: 15.2228
Epoch 9633/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.1008 - root_mean_squared_error: 1.7609 - val_loss: 230.6767 - val_root_mean_squared_error: 15.1880
Epoch 9634/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.1216 - root_mean_squared_error: 1.7668 - val_loss: 231.8663 - val_root_mean_squared_error: 15.2272
Epoch 9635/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.2334 - root_mean_squared_error: 1.7982 - val_loss: 229.9688 - val_root_mean_squared_error: 15.1647
Epoch 9636/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.8669 - root_mean_squared_error

288/288 [==============================] - 1s 2ms/step - loss: 3.7752 - root_mean_squared_error: 1.9430 - val_loss: 232.0419 - val_root_mean_squared_error: 15.2329
Epoch 9722/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.9907 - root_mean_squared_error: 1.7293 - val_loss: 229.2176 - val_root_mean_squared_error: 15.1399
Epoch 9723/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6809 - root_mean_squared_error: 1.6374 - val_loss: 231.9494 - val_root_mean_squared_error: 15.2299
Epoch 9724/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.9993 - root_mean_squared_error: 1.7318 - val_loss: 231.5352 - val_root_mean_squared_error: 15.2163
Epoch 9725/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.1154 - root_mean_squared_error: 1.7651 - val_loss: 231.5934 - val_root_mean_squared_error: 15.2182
Epoch 9726/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.8607 - root_mean_squared_error

288/288 [==============================] - 1s 2ms/step - loss: 2.7260 - root_mean_squared_error: 1.6511 - val_loss: 233.6393 - val_root_mean_squared_error: 15.2853
Epoch 9812/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6517 - root_mean_squared_error: 1.6284 - val_loss: 231.6619 - val_root_mean_squared_error: 15.2204
Epoch 9813/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.9898 - root_mean_squared_error: 1.7291 - val_loss: 228.9244 - val_root_mean_squared_error: 15.1302
Epoch 9814/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.5122 - root_mean_squared_error: 1.8741 - val_loss: 225.6371 - val_root_mean_squared_error: 15.0212
Epoch 9815/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.0752 - root_mean_squared_error: 1.7536 - val_loss: 229.0680 - val_root_mean_squared_error: 15.1350
Epoch 9816/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.9658 - root_mean_squared_error

288/288 [==============================] - 1s 2ms/step - loss: 3.0919 - root_mean_squared_error: 1.7584 - val_loss: 231.7100 - val_root_mean_squared_error: 15.2220
Epoch 9902/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.0130 - root_mean_squared_error: 1.7358 - val_loss: 233.8846 - val_root_mean_squared_error: 15.2933
Epoch 9903/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.9136 - root_mean_squared_error: 1.9783 - val_loss: 230.6786 - val_root_mean_squared_error: 15.1881
Epoch 9904/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.3041 - root_mean_squared_error: 1.8177 - val_loss: 233.3677 - val_root_mean_squared_error: 15.2764
Epoch 9905/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.1266 - root_mean_squared_error: 1.7682 - val_loss: 231.6486 - val_root_mean_squared_error: 15.2200
Epoch 9906/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6776 - root_mean_squared_error

288/288 [==============================] - 1s 2ms/step - loss: 3.1525 - root_mean_squared_error: 1.7755 - val_loss: 231.4135 - val_root_mean_squared_error: 15.2123
Epoch 9992/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.1089 - root_mean_squared_error: 1.7632 - val_loss: 232.7214 - val_root_mean_squared_error: 15.2552
Epoch 9993/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.9886 - root_mean_squared_error: 1.7287 - val_loss: 234.6193 - val_root_mean_squared_error: 15.3173
Epoch 9994/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6900 - root_mean_squared_error: 1.6401 - val_loss: 233.7425 - val_root_mean_squared_error: 15.2886
Epoch 9995/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6199 - root_mean_squared_error: 1.6186 - val_loss: 232.2078 - val_root_mean_squared_error: 15.2384
Epoch 9996/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.4582 - root_mean_squared_error

In [8]:
#saving a model
model.save('long_train_model.keras')

In [9]:
history1 = model.fit(X_train_r_ss, y_train_r, epochs=30000,
                    validation_data=(X_val_r_ss, y_val_r))

Epoch 1/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.4504 - root_mean_squared_error: 1.8575 - val_loss: 234.9339 - val_root_mean_squared_error: 15.3276
Epoch 2/30000
288/288 [==============================] - 0s 2ms/step - loss: 3.7820 - root_mean_squared_error: 1.9447 - val_loss: 235.4863 - val_root_mean_squared_error: 15.3456
Epoch 3/30000
288/288 [==============================] - 0s 2ms/step - loss: 3.0436 - root_mean_squared_error: 1.7446 - val_loss: 231.0083 - val_root_mean_squared_error: 15.1990
Epoch 4/30000
288/288 [==============================] - 0s 2ms/step - loss: 3.0968 - root_mean_squared_error: 1.7598 - val_loss: 236.0880 - val_root_mean_squared_error: 15.3652
Epoch 5/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.9742 - root_mean_squared_error: 1.7246 - val_loss: 233.8972 - val_root_mean_squared_error: 15.2937
Epoch 6/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.7985 - root_mean_squared_error:

Epoch 47/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.9994 - root_mean_squared_error: 1.7319 - val_loss: 232.0780 - val_root_mean_squared_error: 15.2341
Epoch 48/30000
288/288 [==============================] - 0s 2ms/step - loss: 3.2317 - root_mean_squared_error: 1.7977 - val_loss: 231.1440 - val_root_mean_squared_error: 15.2034
Epoch 49/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.2677 - root_mean_squared_error: 1.8077 - val_loss: 232.0074 - val_root_mean_squared_error: 15.2318
Epoch 50/30000
288/288 [==============================] - 0s 2ms/step - loss: 3.1631 - root_mean_squared_error: 1.7785 - val_loss: 231.1059 - val_root_mean_squared_error: 15.2022
Epoch 51/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.1371 - root_mean_squared_error: 1.7712 - val_loss: 230.0379 - val_root_mean_squared_error: 15.1670
Epoch 52/30000
288/288 [==============================] - 0s 2ms/step - loss: 4.1330 - root_mean_squared_

Epoch 93/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.7173 - root_mean_squared_error: 1.6484 - val_loss: 229.5153 - val_root_mean_squared_error: 15.1498
Epoch 94/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.8839 - root_mean_squared_error: 1.6982 - val_loss: 235.1771 - val_root_mean_squared_error: 15.3355
Epoch 95/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.7516 - root_mean_squared_error: 1.6588 - val_loss: 234.3933 - val_root_mean_squared_error: 15.3099
Epoch 96/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.8449 - root_mean_squared_error: 1.6867 - val_loss: 235.9178 - val_root_mean_squared_error: 15.3596
Epoch 97/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.5925 - root_mean_squared_error: 1.8954 - val_loss: 234.4900 - val_root_mean_squared_error: 15.3131
Epoch 98/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.6558 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 3.0609 - root_mean_squared_error: 1.7495 - val_loss: 230.0017 - val_root_mean_squared_error: 15.1658
Epoch 184/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.1999 - root_mean_squared_error: 1.7888 - val_loss: 234.9657 - val_root_mean_squared_error: 15.3286
Epoch 185/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.9874 - root_mean_squared_error: 1.7284 - val_loss: 233.3620 - val_root_mean_squared_error: 15.2762
Epoch 186/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.0399 - root_mean_squared_error: 1.7435 - val_loss: 232.7088 - val_root_mean_squared_error: 15.2548
Epoch 187/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.1694 - root_mean_squared_error: 1.7803 - val_loss: 235.1548 - val_root_mean_squared_error: 15.3348
Epoch 188/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.8895 - root_mean_squared_error: 1.6

288/288 [==============================] - 1s 2ms/step - loss: 2.4393 - root_mean_squared_error: 1.5618 - val_loss: 230.1114 - val_root_mean_squared_error: 15.1694
Epoch 274/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.7841 - root_mean_squared_error: 1.6686 - val_loss: 229.5494 - val_root_mean_squared_error: 15.1509
Epoch 275/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.4822 - root_mean_squared_error: 1.8661 - val_loss: 230.6943 - val_root_mean_squared_error: 15.1886
Epoch 276/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.8045 - root_mean_squared_error: 1.9505 - val_loss: 229.2466 - val_root_mean_squared_error: 15.1409
Epoch 277/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.2714 - root_mean_squared_error: 1.8087 - val_loss: 232.3954 - val_root_mean_squared_error: 15.2445
Epoch 278/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.8739 - root_mean_squared_error: 1.6

...

288/288 [==============================] - 1s 2ms/step - loss: 2.5352 - root_mean_squared_error: 1.5922 - val_loss: 222.7241 - val_root_mean_squared_error: 14.9239
Epoch 29614/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.7970 - root_mean_squared_error: 1.6724 - val_loss: 224.0621 - val_root_mean_squared_error: 14.9687
Epoch 29615/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.5963 - root_mean_squared_error: 1.6113 - val_loss: 224.0271 - val_root_mean_squared_error: 14.9675
Epoch 29616/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6836 - root_mean_squared_error: 1.6382 - val_loss: 224.3943 - val_root_mean_squared_error: 14.9798
Epoch 29617/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4192 - root_mean_squared_error: 1.5554 - val_loss: 222.0490 - val_root_mean_squared_error: 14.9013
Epoch 29618/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.1028 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 2.7523 - root_mean_squared_error: 1.6590 - val_loss: 222.0179 - val_root_mean_squared_error: 14.9003
Epoch 29704/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.7020 - root_mean_squared_error: 1.6438 - val_loss: 223.8407 - val_root_mean_squared_error: 14.9613
Epoch 29705/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6857 - root_mean_squared_error: 1.6388 - val_loss: 223.8344 - val_root_mean_squared_error: 14.9611
Epoch 29706/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4322 - root_mean_squared_error: 1.5595 - val_loss: 224.5502 - val_root_mean_squared_error: 14.9850
Epoch 29707/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.7249 - root_mean_squared_error: 1.6507 - val_loss: 223.3696 - val_root_mean_squared_error: 14.9456
Epoch 29708/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6308 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 2.5270 - root_mean_squared_error: 1.5896 - val_loss: 220.9481 - val_root_mean_squared_error: 14.8643
Epoch 29794/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.5254 - root_mean_squared_error: 1.5891 - val_loss: 222.3569 - val_root_mean_squared_error: 14.9116
Epoch 29795/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.1963 - root_mean_squared_error: 1.7878 - val_loss: 225.7495 - val_root_mean_squared_error: 15.0250
Epoch 29796/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.7178 - root_mean_squared_error: 1.6486 - val_loss: 223.3198 - val_root_mean_squared_error: 14.9439
Epoch 29797/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6970 - root_mean_squared_error: 1.6423 - val_loss: 221.5485 - val_root_mean_squared_error: 14.8845
Epoch 29798/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.1995 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 2.5800 - root_mean_squared_error: 1.6062 - val_loss: 227.8340 - val_root_mean_squared_error: 15.0942
Epoch 29884/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4775 - root_mean_squared_error: 1.5740 - val_loss: 222.4318 - val_root_mean_squared_error: 14.9141
Epoch 29885/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6191 - root_mean_squared_error: 1.6184 - val_loss: 223.0497 - val_root_mean_squared_error: 14.9348
Epoch 29886/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6362 - root_mean_squared_error: 1.6236 - val_loss: 226.6161 - val_root_mean_squared_error: 15.0538
Epoch 29887/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6397 - root_mean_squared_error: 1.6247 - val_loss: 229.6119 - val_root_mean_squared_error: 15.1530
Epoch 29888/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6338 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 2.7447 - root_mean_squared_error: 1.6567 - val_loss: 225.0569 - val_root_mean_squared_error: 15.0019
Epoch 29974/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.0316 - root_mean_squared_error: 1.7412 - val_loss: 224.5207 - val_root_mean_squared_error: 14.9840
Epoch 29975/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.7611 - root_mean_squared_error: 1.6617 - val_loss: 224.9346 - val_root_mean_squared_error: 14.9978
Epoch 29976/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4222 - root_mean_squared_error: 1.5563 - val_loss: 225.9324 - val_root_mean_squared_error: 15.0310
Epoch 29977/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4431 - root_mean_squared_error: 1.5630 - val_loss: 223.3652 - val_root_mean_squared_error: 14.9454
Epoch 29978/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4655 - root_mean_squared_

In [10]:
#saving the model again.  There was marginal improvement overnight.
#saving a model
model.save('long_train_model.keras')